# Initialise & Setup Stakeholder Analysis - 01

In [1]:
# ==== 00a) Interactive Setup + 10-line PEA Summary (with run.yaml update) ====
# - Gradio to input Subject / State / Issue Focus
# - LLM (if key present) to generate a 10-line summary
# - OVERWRITE latest pea_summaries.csv
# - ALSO: update configs/run.yaml -> current_state/current_issue/current_subject
# - Write outputs to BOTH outputs/<slug>-state and outputs/<slug> (avoid path mismatches)

import os, json, re
from pathlib import Path
from datetime import datetime
import pandas as pd
import yaml
import gradio as gr

# -----------------------
# Project root detection
# -----------------------
def find_project_root(max_up=8):
    p = Path.cwd()
    for _ in range(max_up):
        if (p / "configs").exists() and ((p / "src").exists() or (p / "notebooks").exists()):
            return p
        p = p.parent
    return Path.cwd()

ROOT = find_project_root()
print("ROOT ->", ROOT.resolve())

# -----------------------
# OpenAI client (robust)
# -----------------------
def _load_openai_cfg():
    cfg_path = ROOT / "configs" / "config.json"
    cfg = {}
    if cfg_path.exists():
        try:
            with cfg_path.open("r", encoding="utf-8") as f:
                cfg = json.load(f) or {}
        except Exception:
            cfg = {}
    key = (
        os.getenv("OPENAI_API_KEY")
        or os.getenv("OPEN_API_KEY")
        or cfg.get("OPENAI_API_KEY")
        or cfg.get("OPEN_API_KEY")
    )
    if key:
        cfg["OPENAI_API_KEY"] = key
    base = os.getenv("OPENAI_BASE_URL") or cfg.get("ENVIRONMENT_URL") or cfg.get("OPENAI_BASE_URL")
    if base:
        cfg["OPENAI_BASE_URL"] = base
    cfg["MODEL"] = cfg.get("MODEL") or "gpt-4o-mini"
    return cfg

def _openai_client_or_none():
    cfg = _load_openai_cfg()
    api_key = cfg.get("OPENAI_API_KEY")
    if not api_key:
        return None, "No OPENAI_API_KEY (or OPEN_API_KEY) in configs/config.json or environment."
    try:
        from openai import OpenAI
        kwargs = {"api_key": api_key}
        if cfg.get("OPENAI_BASE_URL"):
            kwargs["base_url"] = cfg["OPENAI_BASE_URL"]
        return OpenAI(**kwargs), None
    except Exception as e:
        return None, f"OpenAI client init failed: {e}"

# -----------------------
# Helpers
# -----------------------
def _slugify(s: str) -> str:
    return re.sub(r"[^0-9a-zA-Z]+", "-", (s or "").strip().lower()).strip("-") or "unknown"

def _validated_text(x: str) -> str:
    return (x or "").strip()

def _ensure_output_dirs_for_state(state: str):
    """Return (dir_slug_state, dir_slug) and ensure both exist."""
    slug = _slugify(state)
    d1 = ROOT / "outputs" / f"{slug}-state"
    d2 = ROOT / "outputs" / slug
    d1.mkdir(parents=True, exist_ok=True)
    d2.mkdir(parents=True, exist_ok=True)
    return d1, d2

def _read_run_yaml():
    p = ROOT / "configs" / "run.yaml"
    if p.exists():
        try:
            return yaml.safe_load(p.read_text(encoding="utf-8")) or {}
        except Exception:
            return {}
    return {}

def _atomic_write_text(path: Path, text: str):
    tmp = path.with_suffix(path.suffix + ".tmp")
    tmp.write_text(text, encoding="utf-8")
    tmp.replace(path)

def _update_run_yaml(subject: str, state: str, issue: str):
    """
    Update configs/run.yaml: current_state, current_issue, current_subject.
    Preserve any other keys the file already has.
    """
    cfg = _read_run_yaml()
    if not cfg:
        cfg = {
            "current_state": state,
            "current_issue": issue,
            "current_subject": subject,
            "paths": {
                "data": "data/{state}",
                "outputs": "outputs/{state}",
                "logs": "logs/{state}",
            },
        }
    else:
        cfg["current_state"]  = state
        cfg["current_issue"]  = issue
        cfg["current_subject"] = subject

    run_yaml_path = ROOT / "configs" / "run.yaml"
    _atomic_write_text(run_yaml_path, yaml.safe_dump(cfg, sort_keys=False))
    return run_yaml_path

# -----------------------
# LLM prompt + fallback
# -----------------------
def _build_prompt(subject, state, issue):
    return f"""
You are a Political Economy Analyst.

Produce a crisp, 10-line political economy summary for:
- Subject: {subject}
- Location/State: {state}
- Issue focus: {issue}

Cover:
1) Context & salience in {state}.
2) Key institutions/officeholders (exec, legislature, MDAs).
3) Non-state actors (CSOs/private sector/media/dev partners).
4) Incentives, constraints, veto points.
5) Budget/policy hooks.
6) Windows of opportunity.
7) Risks/pushback.
8) Information/capacity gaps.
9) Likely winners/losers.
10) One-line strategic implication.

Write exactly 10 numbered lines, concise and specific.
""".strip()

def _heuristic_summary(subject, state, issue):
    lines = [
        f"1) {issue.title()} has rising salience in {state} within the {subject.lower()} agenda.",
        "2) Power centers: Governor/ExCo; MDAs (Environment, Works, Water, Agriculture, Planning); Assembly committees.",
        "3) Non-state actors: governance/WASH CSOs, media, contractors, dev partners with climate/infra portfolios.",
        "4) Incentives: visible delivery, fiscal credibility, donor alignment; constraints: revenue space, capacity, elite bargains.",
        "5) Hooks: budget estimates, CAPEX lines, program codes, policy statements, MTSS/SEIF linkages.",
        "6) Windows: procurement cycles, legislative oversight, donor milestones, disaster-season attention spikes.",
        "7) Risks: politicized siting, contractor capture, opacity, pre-election short-termism.",
        "8) Gaps: asset/risk data, O&M budgeting, last-mile delivery, inter-MDA/LGA coordination.",
        f"9) Winners: agencies controlling {issue.lower()} spend; losers: status-quo rent holders.",
        f"10) Strategy: frame {issue.lower()} as fiscal-risk reduction + visible benefits; sequence reforms, broker coalitions, link to budget oversight."
    ]
    return "\n".join(lines)

def llm_pea_summary(subject: str, state: str, issue: str):
    cfg = _load_openai_cfg()
    model = cfg.get("MODEL", "gpt-4o-mini")
    prompt = _build_prompt(subject, state, issue)
    client, err = _openai_client_or_none()
    if client is None:
        header = f"### {subject} • {state} • {issue}\n_(LLM unavailable: {err})_\n"
        return header + "\n" + _heuristic_summary(subject, state, issue)
    try:
        resp = client.chat.completions.create(
            model=model,
            messages=[{"role": "user", "content": prompt}],
            temperature=0.2,
        )
        text = (resp.choices[0].message.content or "").strip()
        if not text:
            raise RuntimeError("Empty response from model.")
        header = f"### {subject} • {state} • {issue}\n"
        return header + "\n" + text
    except Exception as e:
        header = f"### {subject} • {state} • {issue}\n_(LLM error: {e})_\n"
        return header + "\n" + _heuristic_summary(subject, state, issue)

# -----------------------
# Save summary (OVERWRITE) + dual-output dirs + run.yaml update
# -----------------------
def save_pea_summary_overwrite(subject: str, state: str, issue: str, summary_text: str) -> str:
    """
    Overwrite the latest PEA summary CSV in BOTH:
      outputs/<slug>-state/pea_summaries.csv
      outputs/<slug>/pea_summaries.csv
    Also writes timestamped snapshots in each dir.
    Updates configs/run.yaml with current_state/current_issue/current_subject.
    """
    subject = _validated_text(subject)
    state   = _validated_text(state)
    issue   = _validated_text(issue)
    summary = _validated_text(summary_text)

    if not (subject and state and issue and summary):
        raise ValueError("Subject, State, Issue, and Summary must be non-empty.")

    BAD_SNIPPETS = {"pea summary will appear here", "please fill in subject", "llm unavailable", "error", "placeholder"}
    if any(b in summary.lower() for b in BAD_SNIPPETS):
        raise ValueError("Summary looks like a placeholder/error. Generate a real summary before saving.")

    # Ensure both output dirs exist
    dir_slug_state, dir_slug = _ensure_output_dirs_for_state(state)

    ts = datetime.utcnow().isoformat(timespec="seconds") + "Z"
    row = pd.DataFrame([{
        "timestamp_utc": ts,
        "subject": subject,
        "state": state,
        "issue_focus": issue,
        "summary": summary
    }])

    # Write to both locations (OVERWRITE latest)
    latest1 = dir_slug_state / "pea_summaries.csv"
    latest2 = dir_slug / "pea_summaries.csv"
    row.to_csv(latest1, index=False, mode="w")
    row.to_csv(latest2, index=False, mode="w")

    snap1 = dir_slug_state / f"pea_summaries_{ts.replace(':','-')}.csv"
    snap2 = dir_slug / f"pea_summaries_{ts.replace(':','-')}.csv"
    row.to_csv(snap1, index=False)
    row.to_csv(snap2, index=False)

    # Update run.yaml
    run_yaml_path = _update_run_yaml(subject, state, issue)

    return (
        "Saved latest PEA summaries (overwritten):\n"
        f" - {latest1}\n"
        f" - {latest2}\n"
        "Snapshots:\n"
        f" - {snap1}\n"
        f" - {snap2}\n"
        f"Updated run.yaml → {run_yaml_path}"
    )

# -----------------------
# Gradio UI
# -----------------------
with gr.Blocks(title="PEA Setup") as demo:
    gr.Markdown("## Political Economy Analysis — Workbook Parameters")

    with gr.Row():
        subject_tb = gr.Textbox(label="Subject", value="Climate Governance", interactive=True)
        state_tb   = gr.Textbox(label="State/Location", value="Kaduna State", interactive=True)
        issue_tb   = gr.Textbox(label="Issue Focus", value="Flood Control in Zaria", interactive=True)

    summary_state = gr.State("")

    with gr.Row():
        submit_btn = gr.Button("Generate 10-Line PEA Summary", variant="primary", scale=2)

    pea_md = gr.Markdown("")
    save_status = gr.Markdown("")

    def _on_submit(subject, state, issue):
        subject = (subject or "").strip()
        state   = (state or "").strip()
        issue   = (issue or "").strip()
        if not subject or not state or not issue:
            msg = "Please fill in Subject, State, and Issue Focus."
            return msg, msg
        md = llm_pea_summary(subject, state, issue)
        return md, md

    submit_btn.click(
        _on_submit,
        inputs=[subject_tb, state_tb, issue_tb],
        outputs=[pea_md, summary_state],
    )

    with gr.Row():
        save_btn = gr.Button("Save & Finish", variant="primary")
        end_btn  = gr.Button("Finish without Saving", variant="secondary")

    def _on_save(subject, state, issue, summary_text):
        subject = (subject or "").strip()
        state   = (state or "").strip()
        issue   = (issue or "").strip()
        if not (subject and state and issue):
            return "Please fill in Subject, State, and Issue Focus, then press **Generate 10-Line PEA Summary**."
        if not isinstance(summary_text, str) or not summary_text.strip():
            return "No summary to save. Please press **Generate 10-Line PEA Summary** first."
        try:
            msg = save_pea_summary_overwrite(subject, state, issue, summary_text.strip())
            return f"✅ {msg}\n\nYou can now close this tab."
        except Exception as e:
            return f"⚠️ Failed to save: {e}"

    def _on_finish_no_save():
        return "Session finished without saving. You can close this tab."

    save_btn.click(
        _on_save,
        inputs=[subject_tb, state_tb, issue_tb, summary_state],
        outputs=[save_status],
    )
    end_btn.click(
        _on_finish_no_save,
        inputs=[],
        outputs=[save_status],
    )

demo.launch(inline=True, share=False)

ROOT -> /Users/olusojiapampa/Library/Mobile Documents/com~apple~CloudDocs/Documents/Proposals/PACE/PEAIM/PEAIM_clean_full
* Running on local URL:  http://127.0.0.1:7860
* To create a public link, set `share=True` in `launch()`.
